In [1]:
import os
os.chdir("/home/atulgang/Thesis")


In [2]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [3]:
import nltk
from nltk.tokenize import word_tokenize
from stop_words import get_stop_words
from nltk.stem import WordNetLemmatizer
from gensim import corpora, models
import gensim
import glob2
from itertools import chain
import os
import numpy as np
import itertools
import cPickle as pickle
from  scipy.stats import rankdata
import copy
from openpyxl import Workbook
from openpyxl.compat import range
from openpyxl.utils import get_column_letter
from openpyxl import load_workbook
import pandas as pd
from scipy.stats import hmean
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk import pos_tag
from nltk.stem import WordNetLemmatizer

2018-05-04 15:57:04,234 : INFO : 'pattern' package not found; tag filters are not available for English


In [4]:

# WordNet only cares about 5 parts of speech.
# The other parts of speech will be tagged as nouns.

part = {
    'N' : 'n',
    'V' : 'v',
    'J' : 'a',
    'S' : 's',
    'R' : 'r'
}

wnl = WordNetLemmatizer()

def convert_tag(penn_tag):
    '''
    convert_tag() accepts the **first letter** of a Penn part-of-speech tag,
    then uses a dict lookup to convert it to the appropriate WordNet tag.
    '''
    if penn_tag in part.keys():
        return part[penn_tag]
    else:
        # other parts of speech will be tagged as nouns
        return 'n'


def tag_and_lem(element):
    '''
    tag_and_lem() accepts a token list, tags, converts tags,
    lemmatizes, and returns a string
    '''
    # list of tuples [('token', 'tag'), ('token2', 'tag2')...]
    sent = pos_tag(element) # must tag in context
    return [ wnl.lemmatize(sent[k][0], convert_tag(sent[k][1][0])) for k in range(len(sent))]

In [5]:
# ignores everything except english alphabet and  
def only_alphabet(text):
    return ''.join(i for i in text if (ord(i)<123 and ord(i)>96) or (ord(i)<91 and ord(i)>64) or ord(i)==32) 

full_filenames = []
x= ['LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt','LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt' ,'LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt']
for glob_filenames in x:
    glob_filenames = os.path.normpath(glob_filenames)
    for filename in sorted(glob2.glob(glob_filenames)):
        full_filenames.append(filename)
            
filenames = []
x= ['LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt','LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt','LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt' ,'LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt', 'LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt']
for glob_filenames in x:
    glob_filenames = os.path.normpath(glob_filenames)
    for filename in sorted(glob2.glob(glob_filenames)):
        filenames.append(os.path.basename(filename))

In [6]:
en_stop = set(get_stop_words('en'))

# "yield" for each file return token list  i.e list of lists
def files_to_tokens(glob_filenames):
    glob_filenames = os.path.normpath(glob_filenames)
    for filename in sorted(glob2.glob(glob_filenames)):
        f = open(filename)
        #print filename
        # read the whole file as lowercase string
        string = (f.read()).lower()
        try:
            temp = word_tokenize(string)
        except:
            string = string.decode("latin-1")
            temp = word_tokenize(string)
        
        tokens = []
        # tokenize that string
        for word in temp:
            w =  only_alphabet(word).lower()
            if w not in en_stop:
                if w:
                    tokens.append(w)
        tokens = tag_and_lem(tokens)
        yield tokens
        f.close()

        
# yields token list for files specific to courts; needed for creating dictionaries
class texts:
    def DCDRC(self):
        return files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/**/*.txt')
    def NCDRC(self):
        return files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt')
    def SCDRC(self):
        return files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt')
    def DelhiHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt')
    def JharkhandHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt')
    def JodhpurHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt')
    def KolkataHC(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt')
    def SupremeCourt(self):
        return files_to_tokens('LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt')
    def everything(self):
        return chain(self.DCDRC(), self.NCDRC(), self.SCDRC(), self.DelhiHC(),
                     self.JharkhandHC(), self.JodhpurHC(), self.KolkataHC(), self.SupremeCourt())

# yields bow for each file - tuples id,fq ; needed to train models   
class my_corpus:    
    def DCDRC(self):
        for text in files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/DCDRC/*.txt'):
            yield dictionary.doc2bow(text)
    def NCDRC(self):
        for text in files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/NCDRC/**/*.txt'):
            yield dictionary.doc2bow(text)            
    def SCDRC(self):
        for text in files_to_tokens('LegalAdhocTask/ConsumerCourtAdhocdata/SCDRC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def DelhiHC(self):
        for text in files_to_tokens('LegalAdhocTask/SC-HCAdhocData/DelhiHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def JharkhandHC(self):
        for text in files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JharkhandHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def JodhpurHC(self):
        for text in  files_to_tokens('LegalAdhocTask/SC-HCAdhocData/JodhpurHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def KolkataHC(self):
        for text in  files_to_tokens('LegalAdhocTask/SC-HCAdhocData/KolkataHC/**/*.txt'):
            yield dictionary.doc2bow(text)
    def SupremeCourt(self):
        for text in  files_to_tokens('LegalAdhocTask/SC-HCAdhocData/SupremeCourt/**/*.txt'):
            yield dictionary.doc2bow(text)
    def everything(self):
        return chain(self.DCDRC(), self.NCDRC(), self.SCDRC(), self.DelhiHC(),
                     self.JharkhandHC(), self.JodhpurHC(), self.KolkataHC(), self.SupremeCourt())
        
        

In [7]:
#################################### laod the dictinary
dictionary = corpora.Dictionary.load('dict/lem10')

2018-05-04 15:57:21,378 : INFO : loading Dictionary object from dict/lem10
2018-05-04 15:57:21,445 : INFO : loaded dict/lem10


In [8]:
######################################## load BOW
corpus = corpora.MmCorpus('corpus/bow_lem10.mm')

2018-05-04 15:57:21,523 : INFO : loaded corpus index from corpus/bow_lem10.mm.index
2018-05-04 15:57:21,524 : INFO : initializing cython corpus reader from corpus/bow_lem10.mm
2018-05-04 15:57:21,525 : INFO : accepted corpus with 351985 documents, 169716 features, 99651009 non-zero entries


In [9]:
# %%time

# c = texts()
# count = 0
# for x in c.everything():
#     x = [ i for i in x if i in dictionary.token2id]
#     with open(os.path.normpath('Token_corpus2/' + str(count)), 'wb') as fp:
#         pickle.dump(x, fp)
#     count=count+1


In [10]:
def token_corpus(i):
    with open (os.path.normpath('Token_corpus2/' + str(i)), 'rb') as fp:
            itemlist = pickle.load(fp)
            return itemlist   

In [11]:
class iter_token_corpus:
    def __iter__(self):
        for i in xrange(0, 351985):
            with open (os.path.normpath('Token_corpus2/' + str(i)), 'rb') as fp:
                itemlist = pickle.load(fp)
                yield itemlist

In [12]:
%%time
model = gensim.models.fasttext.FastText(iter_token_corpus(), hs = 1, sg = 1, size=300, iter = 20, min_count=0, sample=.00001, workers=8)

2018-05-04 15:57:22,470 : INFO : collecting all words and their counts
2018-05-04 15:57:22,473 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2018-05-04 15:57:34,511 : INFO : PROGRESS: at sentence #10000, processed 12250127 words, keeping 69492 word types
2018-05-04 15:57:45,088 : INFO : PROGRESS: at sentence #20000, processed 23019662 words, keeping 93100 word types
2018-05-04 15:57:55,926 : INFO : PROGRESS: at sentence #30000, processed 33121221 words, keeping 108174 word types
2018-05-04 15:58:04,352 : INFO : PROGRESS: at sentence #40000, processed 41771479 words, keeping 121160 word types
2018-05-04 15:58:10,999 : INFO : PROGRESS: at sentence #50000, processed 48600564 words, keeping 127318 word types
2018-05-04 15:58:17,392 : INFO : PROGRESS: at sentence #60000, processed 54839174 words, keeping 133012 word types
2018-05-04 15:58:22,830 : INFO : PROGRESS: at sentence #70000, processed 60283301 words, keeping 136653 word types
2018-05-04 15:58:29,422 : I

2018-05-04 16:03:49,418 : INFO : EPOCH 1 - PROGRESS: at 0.78% examples, 22883 words/s, in_qsize 6, out_qsize 0
2018-05-04 16:03:50,446 : INFO : EPOCH 1 - PROGRESS: at 0.83% examples, 22943 words/s, in_qsize 6, out_qsize 1
2018-05-04 16:03:51,479 : INFO : EPOCH 1 - PROGRESS: at 0.85% examples, 22774 words/s, in_qsize 9, out_qsize 0
2018-05-04 16:03:52,550 : INFO : EPOCH 1 - PROGRESS: at 0.87% examples, 22698 words/s, in_qsize 12, out_qsize 0
2018-05-04 16:03:53,686 : INFO : EPOCH 1 - PROGRESS: at 0.89% examples, 22580 words/s, in_qsize 9, out_qsize 0
2018-05-04 16:03:54,715 : INFO : EPOCH 1 - PROGRESS: at 0.91% examples, 22547 words/s, in_qsize 11, out_qsize 0
2018-05-04 16:03:55,764 : INFO : EPOCH 1 - PROGRESS: at 0.92% examples, 22309 words/s, in_qsize 14, out_qsize 0
2018-05-04 16:03:56,779 : INFO : EPOCH 1 - PROGRESS: at 0.94% examples, 22382 words/s, in_qsize 11, out_qsize 0
2018-05-04 16:03:57,913 : INFO : EPOCH 1 - PROGRESS: at 0.95% examples, 22028 words/s, in_qsize 15, out_qsiz

2018-05-04 16:05:11,175 : INFO : EPOCH 1 - PROGRESS: at 2.08% examples, 21762 words/s, in_qsize 16, out_qsize 0
2018-05-04 16:05:12,192 : INFO : EPOCH 1 - PROGRESS: at 2.09% examples, 21824 words/s, in_qsize 14, out_qsize 0
2018-05-04 16:05:13,280 : INFO : EPOCH 1 - PROGRESS: at 2.09% examples, 21809 words/s, in_qsize 9, out_qsize 2
2018-05-04 16:05:14,462 : INFO : EPOCH 1 - PROGRESS: at 2.10% examples, 21722 words/s, in_qsize 15, out_qsize 0
2018-05-04 16:05:15,633 : INFO : EPOCH 1 - PROGRESS: at 2.12% examples, 21746 words/s, in_qsize 14, out_qsize 0
2018-05-04 16:05:16,811 : INFO : EPOCH 1 - PROGRESS: at 2.13% examples, 21803 words/s, in_qsize 10, out_qsize 0
2018-05-04 16:05:17,875 : INFO : EPOCH 1 - PROGRESS: at 2.15% examples, 21797 words/s, in_qsize 16, out_qsize 0
2018-05-04 16:05:19,199 : INFO : EPOCH 1 - PROGRESS: at 2.17% examples, 21776 words/s, in_qsize 15, out_qsize 0
2018-05-04 16:05:20,402 : INFO : EPOCH 1 - PROGRESS: at 2.19% examples, 21774 words/s, in_qsize 16, out_q

2018-05-04 16:06:35,044 : INFO : EPOCH 1 - PROGRESS: at 3.42% examples, 21158 words/s, in_qsize 6, out_qsize 0
2018-05-04 16:06:36,159 : INFO : EPOCH 1 - PROGRESS: at 3.44% examples, 21165 words/s, in_qsize 10, out_qsize 0
2018-05-04 16:06:37,171 : INFO : EPOCH 1 - PROGRESS: at 3.46% examples, 21157 words/s, in_qsize 13, out_qsize 0
2018-05-04 16:06:38,204 : INFO : EPOCH 1 - PROGRESS: at 3.49% examples, 21154 words/s, in_qsize 15, out_qsize 0
2018-05-04 16:06:39,377 : INFO : EPOCH 1 - PROGRESS: at 3.51% examples, 21127 words/s, in_qsize 16, out_qsize 0
2018-05-04 16:06:40,473 : INFO : EPOCH 1 - PROGRESS: at 3.54% examples, 21142 words/s, in_qsize 13, out_qsize 0
2018-05-04 16:06:41,546 : INFO : EPOCH 1 - PROGRESS: at 3.57% examples, 21146 words/s, in_qsize 10, out_qsize 0
2018-05-04 16:06:42,554 : INFO : EPOCH 1 - PROGRESS: at 3.59% examples, 21156 words/s, in_qsize 7, out_qsize 0
2018-05-04 16:06:43,574 : INFO : EPOCH 1 - PROGRESS: at 3.62% examples, 21154 words/s, in_qsize 8, out_qsi

2018-05-04 16:07:59,312 : INFO : EPOCH 1 - PROGRESS: at 4.86% examples, 20693 words/s, in_qsize 13, out_qsize 0
2018-05-04 16:08:00,691 : INFO : EPOCH 1 - PROGRESS: at 4.88% examples, 20670 words/s, in_qsize 13, out_qsize 0
2018-05-04 16:08:01,814 : INFO : EPOCH 1 - PROGRESS: at 4.90% examples, 20665 words/s, in_qsize 13, out_qsize 2
2018-05-04 16:08:02,847 : INFO : EPOCH 1 - PROGRESS: at 4.93% examples, 20700 words/s, in_qsize 15, out_qsize 0
2018-05-04 16:08:03,934 : INFO : EPOCH 1 - PROGRESS: at 4.95% examples, 20696 words/s, in_qsize 14, out_qsize 0
2018-05-04 16:08:05,038 : INFO : EPOCH 1 - PROGRESS: at 4.97% examples, 20681 words/s, in_qsize 16, out_qsize 0
2018-05-04 16:08:06,509 : INFO : EPOCH 1 - PROGRESS: at 5.00% examples, 20684 words/s, in_qsize 15, out_qsize 0
2018-05-04 16:08:07,446 : INFO : EPOCH 1 - PROGRESS: at 5.03% examples, 20687 words/s, in_qsize 15, out_qsize 0
2018-05-04 16:08:08,545 : INFO : EPOCH 1 - PROGRESS: at 5.05% examples, 20674 words/s, in_qsize 14, out_

...

2018-05-05 07:51:09,959 : INFO : EPOCH 20 - PROGRESS: at 89.33% examples, 71369 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:11,008 : INFO : EPOCH 20 - PROGRESS: at 89.51% examples, 71368 words/s, in_qsize 0, out_qsize 1
2018-05-05 07:51:12,016 : INFO : EPOCH 20 - PROGRESS: at 89.63% examples, 71372 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:13,036 : INFO : EPOCH 20 - PROGRESS: at 89.78% examples, 71372 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:14,111 : INFO : EPOCH 20 - PROGRESS: at 89.91% examples, 71378 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:15,122 : INFO : EPOCH 20 - PROGRESS: at 90.14% examples, 71384 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:16,152 : INFO : EPOCH 20 - PROGRESS: at 90.36% examples, 71384 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:17,173 : INFO : EPOCH 20 - PROGRESS: at 90.56% examples, 71388 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:51:18,208 : INFO : EPOCH 20 - PROGRESS: at 90.65% examples, 71386 words/s, in_qsiz

2018-05-05 07:52:25,514 : INFO : EPOCH 20 - PROGRESS: at 92.99% examples, 71414 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:26,546 : INFO : EPOCH 20 - PROGRESS: at 93.02% examples, 71421 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:27,555 : INFO : EPOCH 20 - PROGRESS: at 93.05% examples, 71423 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:28,579 : INFO : EPOCH 20 - PROGRESS: at 93.07% examples, 71424 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:29,585 : INFO : EPOCH 20 - PROGRESS: at 93.10% examples, 71412 words/s, in_qsize 3, out_qsize 0
2018-05-05 07:52:30,639 : INFO : EPOCH 20 - PROGRESS: at 93.13% examples, 71422 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:31,660 : INFO : EPOCH 20 - PROGRESS: at 93.16% examples, 71417 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:32,668 : INFO : EPOCH 20 - PROGRESS: at 93.19% examples, 71424 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:52:33,669 : INFO : EPOCH 20 - PROGRESS: at 93.22% examples, 71424 words/s, in_qsiz

2018-05-05 07:53:40,798 : INFO : EPOCH 20 - PROGRESS: at 95.30% examples, 71461 words/s, in_qsize 0, out_qsize 1
2018-05-05 07:53:41,790 : INFO : EPOCH 20 - PROGRESS: at 95.35% examples, 71464 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:53:42,827 : INFO : EPOCH 20 - PROGRESS: at 95.43% examples, 71468 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:53:43,858 : INFO : EPOCH 20 - PROGRESS: at 95.50% examples, 71471 words/s, in_qsize 0, out_qsize 1
2018-05-05 07:53:44,889 : INFO : EPOCH 20 - PROGRESS: at 95.56% examples, 71470 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:53:45,973 : INFO : EPOCH 20 - PROGRESS: at 95.64% examples, 71472 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:53:47,004 : INFO : EPOCH 20 - PROGRESS: at 95.71% examples, 71473 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:53:48,034 : INFO : EPOCH 20 - PROGRESS: at 95.76% examples, 71474 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:53:49,058 : INFO : EPOCH 20 - PROGRESS: at 95.82% examples, 71475 words/s, in_qsiz

2018-05-05 07:54:56,685 : INFO : EPOCH 20 - PROGRESS: at 99.04% examples, 71475 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:54:57,677 : INFO : EPOCH 20 - PROGRESS: at 99.09% examples, 71476 words/s, in_qsize 0, out_qsize 1
2018-05-05 07:54:58,726 : INFO : EPOCH 20 - PROGRESS: at 99.15% examples, 71475 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:54:59,728 : INFO : EPOCH 20 - PROGRESS: at 99.24% examples, 71478 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:55:00,780 : INFO : EPOCH 20 - PROGRESS: at 99.28% examples, 71478 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:55:01,783 : INFO : EPOCH 20 - PROGRESS: at 99.30% examples, 71463 words/s, in_qsize 0, out_qsize 3
2018-05-05 07:55:02,814 : INFO : EPOCH 20 - PROGRESS: at 99.33% examples, 71472 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:55:03,843 : INFO : EPOCH 20 - PROGRESS: at 99.37% examples, 71474 words/s, in_qsize 0, out_qsize 0
2018-05-05 07:55:04,860 : INFO : EPOCH 20 - PROGRESS: at 99.41% examples, 71478 words/s, in_qsiz

CPU times: user 2d 58min 58s, sys: 20min 32s, total: 2d 1h 19min 31s
Wall time: 15h 58min 7s


In [13]:
model.save('py_models/FT_SG')

2018-05-05 07:55:30,384 : INFO : saving FastText object under py_models/FT_SG, separately None
2018-05-05 07:55:30,385 : INFO : storing np array 'vectors' to py_models/FT_SG.wv.vectors.npy
2018-05-05 07:55:30,501 : INFO : not storing attribute buckets_word
2018-05-05 07:55:30,502 : INFO : storing np array 'vectors_ngrams' to py_models/FT_SG.wv.vectors_ngrams.npy
2018-05-05 07:55:31,349 : INFO : not storing attribute vectors_norm
2018-05-05 07:55:31,350 : INFO : not storing attribute vectors_ngrams_norm
2018-05-05 07:55:31,351 : INFO : storing np array 'vectors_vocab' to py_models/FT_SG.wv.vectors_vocab.npy
2018-05-05 07:55:32,036 : INFO : not storing attribute vectors_vocab_norm
2018-05-05 07:55:32,037 : INFO : storing np array 'syn1neg' to py_models/FT_SG.trainables.syn1neg.npy
2018-05-05 07:55:32,687 : INFO : storing np array 'syn1' to py_models/FT_SG.trainables.syn1.npy
2018-05-05 07:55:33,306 : INFO : storing np array 'vectors_ngrams_lockf' to py_models/FT_SG.trainables.vectors_ngr

In [14]:
model = gensim.models.Word2Vec.load('py_models/FT_SG')

2018-05-05 07:55:41,138 : INFO : loading Word2Vec object from py_models/FT_SG
2018-05-05 07:55:43,088 : INFO : loading vocabulary recursively from py_models/FT_SG.vocabulary.* with mmap=None
2018-05-05 07:55:43,088 : INFO : loading wv recursively from py_models/FT_SG.wv.* with mmap=None
2018-05-05 07:55:43,089 : INFO : loading vectors from py_models/FT_SG.wv.vectors.npy with mmap=None
2018-05-05 07:55:44,369 : INFO : loading vectors_ngrams from py_models/FT_SG.wv.vectors_ngrams.npy with mmap=None
2018-05-05 07:55:45,862 : INFO : loading vectors_vocab from py_models/FT_SG.wv.vectors_vocab.npy with mmap=None
2018-05-05 07:55:50,156 : INFO : setting ignored attribute buckets_word to None
2018-05-05 07:55:50,156 : INFO : setting ignored attribute vectors_norm to None
2018-05-05 07:55:50,157 : INFO : setting ignored attribute vectors_ngrams_norm to None
2018-05-05 07:55:50,158 : INFO : setting ignored attribute vectors_vocab_norm to None
2018-05-05 07:55:50,158 : INFO : loading trainables r

In [ ]:
# x.doesnt_match(words)

# #     Which word from the given list doesn’t go with the others?
# #     Parameters:	words – List of words
# #     Returns:	The word further away from the mean of all words.
# #     Return type:	str

# x.index2word
# ### list of words in the sorted order of their frequency 

# y = x.vocab['parti']
# y.count
# # find freq. of any word


# x.most_similar_cosmul(positive=None, negative=None, topn=10)
# # Find the top-N most similar words, using the multiplicative combination objective proposed by 
# # Omer Levy and Yoav Goldberg.Positive words still contribute positively towards the similarity, negative words 
# # negatively, but with less susceptibility to one large distance dominating the calculation.

# x.most_similar_to_given(entity1, entities_list)
# #    Return the entity from entities_list most similar to entity1.

# x.n_similarity(ws1, ws2)
# #Compute cosine similarity between two sets of words


# x.similar_by_vector(x['fit'], topn=10, restrict_vocab=None)
# # closest vectors
# # if topn is False, similar_by_vector returns the vector of similarity scores.

# x.similar_by_word(word, topn=10, restrict_vocab=None)
# #  Find the top-N most similar words.

# x.similarity(w1, w2)
# #Compute cosine similarity between two words.

# x.wmdistance(doc1, doc2)
# # word movers distance

# y = x.vocab['parti']
# y.count
# #freq in corpus

In [16]:
%%time

import math
from six import iteritems
from six.moves import xrange
idf = {}
for word, freq in dictionary.dfs.iteritems():
    idf[dictionary[word]] = math.log(dictionary.num_docs) - math.log(freq)


CPU times: user 316 ms, sys: 16 ms, total: 332 ms
Wall time: 308 ms


In [17]:
# get the query truth in dictionary
query_truth = {}
for i in range(1,11):
    query_truth[str(i)]=[]
    
    
f = open('LegalAdhocTask/Consumer.qrels')
lines = [line.rstrip('\n').split("\t") for line in f]
for line in lines:
    del line[1]
    query_truth[line[0]].append(line[1:])


In [18]:
w2v = model.wv
def vec(document):
    return np.add.reduce([idf[i]*w2v[i] for i in document if i in dictionary.token2id])

In [19]:
%%time
doc_vec = []
for x in iter_token_corpus():
    x = vec(x)
    doc_vec.append(x)

CPU times: user 45min 26s, sys: 11.2 s, total: 45min 38s
Wall time: 55min 50s


In [20]:
from scipy.spatial.distance import cosine
def get_scores(query):
    scores = []
    i = 0
    query = vec(query)
    for x in doc_vec:
        if isinstance(x, np.ndarray):
            score = 1 - cosine(x, query)
        else:
            score = -1000
        scores.append(score)
    return scores

In [21]:
%%time
results = copy.deepcopy(query_truth)

sim_list = [0]
rank_list = [0]
queries = [0]
for i,query in enumerate(files_to_tokens('LegalAdhocTask/q*.txt')):
    queries.append(query)
    sims = get_scores(query)
    sim_list.append(sims)
    # rank of every document wrt similarity
    ranks = rankdata(sims, method='ordinal')
    ranks= len(ranks)+1 - ranks 
    rank_list.append(ranks)
    
    # update the query truth tuples with similarity score and the ranks
    for x in results[str(i+1)]:
        x.append(sims[filenames.index(x[0]+'.txt')])
        x.append(ranks[filenames.index(x[0]+'.txt')])
        

CPU times: user 2min 37s, sys: 1.39 s, total: 2min 39s
Wall time: 2min 55s


In [22]:
results

{'1': [['ConsumerCourt_DCDRC_100385', '1', 0.82787024974823, 2516],
  ['ConsumerCourt_DCDRC_106530', '0', 0.7742335796356201, 21450],
  ['ConsumerCourt_DCDRC_107608', '1', 0.8378077745437622, 1457],
  ['ConsumerCourt_DCDRC_114291', '1', 0.8432956337928772, 1018],
  ['ConsumerCourt_DCDRC_114382', '1', 0.8312199115753174, 2120],
  ['ConsumerCourt_DCDRC_118185', '1', 0.8668022751808167, 90],
  ['ConsumerCourt_DCDRC_130318', '0', 0.8340700268745422, 1821],
  ['ConsumerCourt_DCDRC_130570', '1', 0.8522811532020569, 482],
  ['ConsumerCourt_DCDRC_131146', '1', 0.8708832859992981, 53],
  ['ConsumerCourt_DCDRC_131717', '1', 0.8536918759346008, 421],
  ['ConsumerCourt_DCDRC_131741', '1', 0.8480263352394104, 681],
  ['ConsumerCourt_DCDRC_131818', '1', 0.8457317352294922, 833],
  ['ConsumerCourt_DCDRC_131950', '0', 0.8424860239028931, 1078],
  ['ConsumerCourt_DCDRC_131972', '0', 0.8672059774398804, 87],
  ['ConsumerCourt_DCDRC_132932', '0', 0.8817082643508911, 5],
  ['ConsumerCourt_DCDRC_133592', '

In [23]:
model_name = 'FT_SG_IDF'

with open('py_results/' + model_name + 'sim_list.pkl', 'wb') as output:
    pickle.dump(sim_list, output, pickle.HIGHEST_PROTOCOL)
with open('py_results/' + model_name + 'rank_list.pkl', 'wb') as output:
    pickle.dump(rank_list, output, pickle.HIGHEST_PROTOCOL)


In [24]:
# Store results in 1st sheet


wb = Workbook()
dest_filename = 'result_excel/' + model_name + '.xlsx'
ws1 = wb.active
ws1.title = "ground_truth"
ws1.append(['Query','Filename', 'Relevance', 'Score', 'Rank'])
for key,value in results.iteritems():
    for i in value:
        ws1.append([int(key)]+ i)

wb.save(filename = dest_filename)

#Query wise (F score)

import pandas as pd

f = pd.ExcelFile(dest_filename)

from scipy.stats import hmean



places = 4
wb = load_workbook(dest_filename)
ws1 = wb.create_sheet(title="evaluation_Qwise")

ws1.append(['Query','Docs considered', 'Precision/Recall', 'Model', 1, 5 ,10, 25, 50, 100, 500, 1000])

k = [1.0, 5.0 ,10.0, 25.0, 50.0, 100.0, 500.0, 1000.0]
for sheet in f.sheet_names:
    if(sheet == "evaluation"):
        continue
    for q in np.arange(1,11):

        x = f.parse(sheet)
        x = x[x['Query'] == q]
        total_1 = (float)(x[x['Relevance'] == 1].shape[0])
        total_0 = (float)(x[x['Relevance'] == 0].shape[0])
        total = (float)(x.shape[0])
        
        ####  repitition due to complication in considering both 1 & 0 relevance
        # precision 1
        row = [q, 1, 'P', model_name ]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 1 , x['Rank'] <= i)].shape[0]/i)
        ws1.append(row);
        p1 = row;
        # precision 0
        row = [q, 0, 'P', model_name ]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 0 , x['Rank'] <= i)].shape[0]/i)    
        ws1.append(row);
        p0 = row;
        #precision 10
        row = [q, 10, 'P', model_name]
        for i in k:
            row.append(x[x['Rank'] <= i].shape[0]/i)  
        ws1.append(row);
        p10 = row;  
        
        
        # recall 1
        row = [q, 1, 'R', model_name]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 1 , x['Rank'] <= i)].shape[0]/total_1)
            row[-1] = round(row[-1],places)
        ws1.append(row);
        r1 = row;    
        # recall 0
        row = [q, 0, 'R', model_name ]
        for i in k:
            row.append(x[np.logical_and(x['Relevance'] == 0 , x['Rank'] <= i)].shape[0]/total_0)
            row[-1] = round(row[-1],places)
        ws1.append(row);
        r0 = row;
        #recall 10
        row = [q, 10, 'R', model_name ]
        for i in k:
            row.append(x[x['Rank'] <= i].shape[0]/total)
            row[-1] = round(row[-1],places)
        ws1.append(row);
        r10 = row;      


        # F 1
        row = [q, 1, 'F', model_name ]
        for i in range(-len(k), 0, 1):
            if p1[i] == 0.0 :
                row.append(0.0)
            else:
                row.append(hmean([p1[i],r1[i]]))
            row[-1] = round(row[-1],places)
        ws1.append(row);

        # F 0
        row = [q, 0, 'F', model_name]
        for i in range(-len(k), 0, 1):
            if p0[i] == 0.0:
                row.append(0.0)
            else:
                row.append(hmean([p0[i],r0[i]]))
            row[-1] = round(row[-1],places)
        ws1.append(row);

        # F 10
        row = [q, 10, 'F', model_name]
        for i in range(-len(k), 0, 1):
            if p10[i] == 0.0:
                row.append(0.0)
            else:
                row.append(hmean([p10[i],r10[i]]))
            row[-1] = round(row[-1],places)
        ws1.append(row);
        
wb.save(filename = dest_filename)


#Query wise Average precision
# precision sum
def p_sum(z):
    z = z.copy()  
    z.sort_values(inplace=True)
    result = 0
    for i,val in enumerate(z):
        result += (i+1)/float(val) 
    return result


import pandas as pd

f = pd.ExcelFile(dest_filename)

from scipy.stats import hmean


places = 4
wb = load_workbook(dest_filename)
ws1 = wb.create_sheet(title="AP_Qwise")

ws1.append(['Query','Docs considered', 'Precision/Recall', 'Model', 1, 5 ,10, 25, 50, 100, 500, 1000])


for sheet in f.sheet_names:    
    if(sheet == "evaluation"or sheet == "evaluation_Qwise"):
        continue
    for q in np.arange(1,11):
        x = f.parse(sheet)
        x = x[x['Query'] == q]
        total = {}
        total[1] = (float)(x[x['Relevance'] == 1].shape[0])
        total[0] = (float)(x[x['Relevance'] == 0].shape[0])
        total[10] = (float)(x.shape[0])
        
        for rel in [1,0]:
            # precision 1
            row = [q, rel, 'AP', model_name ]
            for i in [1.0, 5.0, 10.0, 25.0, 50.0, 100.0, 500.0, 1000.0]:
                row.append(p_sum(x[np.logical_and(x['Relevance'] == rel, x['Rank'] <= i)]['Rank'])/total[rel])
            ws1.append(row);

        row = [q, 10, 'AP', model_name ]
        for i in [1.0, 5.0, 10.0, 25.0, 50.0, 100.0, 500.0, 1000.0]:
            row.append(p_sum(x[x['Rank'] <= i]['Rank'])/total[10])
        ws1.append(row);
wb.save(filename = dest_filename)

In [26]:
def append_df_to_excel(filename, df, sheet_name='Sheet1', startrow=None,
                       truncate_sheet=False, 
                       **to_excel_kwargs):
    """
    Append a DataFrame [df] to existing Excel file [filename]
    into [sheet_name] Sheet.
    If [filename] doesn't exist, then this function will create it.

    Parameters:
      filename : File path or existing ExcelWriter
                 (Example: '/path/to/file.xlsx')
      df : dataframe to save to workbook
      sheet_name : Name of sheet which will contain DataFrame.
                   (default: 'Sheet1')
      startrow : upper left cell row to dump data frame.
                 Per default (startrow=None) calculate the last row
                 in the existing DF and write to the next row...
      truncate_sheet : truncate (remove and recreate) [sheet_name]
                       before writing DataFrame to Excel file
      to_excel_kwargs : arguments which will be passed to `DataFrame.to_excel()`
                        [can be dictionary]

    Returns: None
    """
    from openpyxl import load_workbook

    # ignore [engine] parameter if it was passed
    if 'engine' in to_excel_kwargs:
        to_excel_kwargs.pop('engine')

    writer = pd.ExcelWriter(filename, engine='openpyxl')

    try:
        # try to open an existing workbook
        writer.book = load_workbook(filename)

        # get the last row in the existing Excel sheet
        # if it was not specified explicitly
        if startrow is None and sheet_name in writer.book.sheetnames:
            startrow = writer.book[sheet_name].max_row

        # truncate sheet
        if truncate_sheet and sheet_name in writer.book.sheetnames:
            # index of [sheet_name] sheet
            idx = writer.book.sheetnames.index(sheet_name)
            # remove [sheet_name]
            writer.book.remove(writer.book.worksheets[idx])
            # create an empty sheet [sheet_name] using old index
            writer.book.create_sheet(sheet_name, idx)

        # copy existing sheets
        writer.sheets = {ws.title:ws for ws in writer.book.worksheets}
    except FileNotFoundError:
        # file does not exist yet, we will create it
        pass

    if startrow is None:
        startrow = 0

    # write out the new sheet
    df.to_excel(writer, sheet_name, startrow=startrow, index= False, header = False, **to_excel_kwargs)

    # save the workbook
    writer.save()

    
f = pd.ExcelFile(dest_filename)
sec_dest = 'result_excel/all_results.xlsx'
f2 = pd.ExcelFile(sec_dest)
append_df_to_excel(sec_dest, f.parse(1), sheet_name= f2.sheet_names[0])
append_df_to_excel(sec_dest, f.parse(2), sheet_name= f2.sheet_names[1])

In [ ]:
############################################################

In [ ]:
def Top_x(x, R):
    R = list(R)
    x_names = []
    for i in range(x):
        x_names.append(filenames[R.index(i + 1)].strip('.txt'))
    return x_names
    
    

In [ ]:
def score_stat(word, freq, index):
    index_doc = dict(bm25.corpus[index])
    word = dictionary.doc2bow([word])[0][0]
    idf = bm25.idf[word] if bm25.idf[word] >= 0 else EPSILON * average_idf
    score = freq*((idf * index_doc[word] * (PARAM_K1 + 1)
              / (index_doc[word] + PARAM_K1 * (1 - PARAM_B + PARAM_B * doc_len[index] / bm25.avgdl))))
    return (index_doc[word], score)

In [ ]:
wb = Workbook()
dest_filename = 'Temp.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)
def common_words(q, F):
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    index = filenames.index(F + '.txt')
    index_doc = dict(bm25.corpus[index])
    row = []
    for word, freq in  zip(q_words, q_freq):
        w = dictionary.doc2bow([word])[0][0]
        if w in index_doc: 
            f, s = score_stat(word, freq, index)
            row.append([word + ', ' + str(round(bm25.idf[w], 2)), freq, f,  round( (s*100)/sim_list[q][index], 1)])  
    row.sort(key = lambda x: (x[3],x[1],x[2]), reverse = True)
    wb = load_workbook('Temp.xlsx')
    ws = wb.create_sheet(title=str(q) + F)
    ws.append(['word,idf', 'Query freq', 'freq', '% score'])
    for i in row:
        ws.append(i)
    wb.save(filename = 'Temp.xlsx')


In [ ]:
f = open("toberead.txt", 'r') 
count = 0
q = 1
for i in f:
    if i == '\n':
        continue
    count = count + 1
    common_words(q, i.strip())
    if count % 5 == 0:
        q = q + 1


In [ ]:
for i in files_to_tokens(full_filenames[filenames.index(doc + '.txt')]):
    for j in i:
        print j

In [ ]:
doc = 'ConsumerCourt_SCDRC_30176'
corpus[]

In [ ]:
common_words(1, 'ConsumerCourt_DCDRC_41588')

In [ ]:
df = pd.DataFrame(index= None, columns=['words','pair'])


In [ ]:
df

In [ ]:
print df

In [ ]:
df.append(['lol', ('we','wew')])

In [ ]:
def uncommon_words(q, filename)

In [ ]:
# Store results in 1st sheet
wb = Workbook()
dest_filename = 'Explore_BM25.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)

wb = load_workbook('Explore_BM25.xlsx')

for q in range(1, 11):
    ws = wb.create_sheet(title="q" + str(q))
    #x_names = Top_x(10, rank_list[q])
    top_row = ['Doc Name', 'Rel', 'Doc Length', ' Rank', 'Score']
    sec_row = [' ']*5
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    ws.append(top_row + [i[0]  for i in temp])
    ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    
    #continue
    doc_list = [i[0] for i in query_truth[str(q)]] + Top_x(10, rank_list[q])
    doc_list = list((set(doc_list)))
    doc_list.sort(key = lambda doc : rank_list[q][filenames.index(doc + '.txt')])
    doc_row = []
    for doc in doc_list:
        temp  = [doc]
        rel_dic = dict(query_truth[str(q)])
        if doc in rel_dic:
            temp.append(rel_dic[doc])
        else:
            temp.append('Not')
        temp.append(doc_len[filenames.index(doc + '.txt')])
        temp.append(rank_list[q][filenames.index(doc + '.txt')])
        temp.append(round(sim_list[q][filenames.index(doc + '.txt')], 2))
        doc_row.append(temp)

    for row in doc_row:
        index = filenames.index(row[0] + '.txt')
        index_doc = dict(bm25.corpus[index])
        
        for word, freq in  zip(q_words, q_freq):
            if dictionary.doc2bow([word])[0][0] in index_doc: 
                f, s = score_stat(word, freq, index)
                row.append( str(f) + ', ' +  str(round( (s*100)/sim_list[q][index], 1) ))
            else:
                row.append('X')
        ws.append(row)
        ws.append([])        
wb.save(filename = dest_filename)

In [ ]:
# Store results in 1st sheet
wb = Workbook()
dest_filename = 'Explore_BM25_uncom.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)



wb = load_workbook('Explore_BM25_uncom.xlsx')

for q in range(1, 11):
    ws = wb.create_sheet(title="q" + str(q))
    #x_names = Top_x(10, rank_list[q])
    top_row = ['Doc Name', 'Rel', 'Doc Length', ' Rank', 'Score']
    sec_row = [' ']*5
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    ws.append(top_row + [i[0]  for i in temp])
    ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    
    #continue
    doc_list = [i[0] for i in query_truth[str(q)]] + Top_x(10, rank_list[q])
    doc_list = list((set(doc_list)))
    doc_list.sort(key = lambda doc : rank_list[q][filenames.index(doc + '.txt')])
    doc_row = []
    for doc in doc_list:
        temp  = [doc]
        rel_dic = dict(query_truth[str(q)])
        if doc in rel_dic:
            temp.append(rel_dic[doc])
        else:
            temp.append('Not')
        temp.append(doc_len[filenames.index(doc + '.txt')])
        temp.append(rank_list[q][filenames.index(doc + '.txt')])
        temp.append(round(sim_list[q][filenames.index(doc + '.txt')], 2))
        doc_row.append(temp)

    for row in doc_row:
        index = filenames.index(row[0] + '.txt')
        index_doc = dict(bm25.corpus[index])
        
#         for word, freq in  zip(q_words, q_freq):
#             if dictionary.doc2bow([word])[0][0] in index_doc: 
#                 f, s = score_stat(word, freq, index)
#                 row.append( str(f) + ', ' +  str(round( (s*100)/sim_list[q][index], 1) ))
#             else:
#                 row.append('X')
        #ws.append(row)
        
        sec_row = [' ']*5
        temp = []
        for word, freq in index_doc.iteritems():
            if dictionary[word] not in q_words:
                temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
        ws.append(row + [i[0]  for i in temp])
        ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
        ws.append([])        
wb.save(filename = dest_filename)

In [ ]:
# Store results in 1st sheet
wb = Workbook()
dest_filename = 'Explore_BM25_all.xlsx'
ws = wb.active
ws.title = "Blank"
#ws.append([(2.2,2.2)])
wb.save(filename = dest_filename)



wb = load_workbook('Explore_BM25_all.xlsx')

for q in range(1, 11):
    ws = wb.create_sheet(title="q" + str(q))
    #x_names = Top_x(10, rank_list[q])
    top_row = ['Doc Name', 'Rel', 'Doc Length', ' Rank', 'Score']
    sec_row = [' ']*5
    temp = []
    for word, freq in dictionary.doc2bow(queries[q]) :
        temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
    temp.sort(key=lambda x: (x[2],x[1]), reverse=True)
    ws.append(top_row + [i[0]  for i in temp])
    ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
    q_words = [i[0]  for i in temp]
    q_freq = [i[1]  for i in temp]
    
    #continue
    doc_list = [i[0] for i in query_truth[str(q)]] + Top_x(10, rank_list[q])
    doc_list = list((set(doc_list)))
    doc_list.sort(key = lambda doc : rank_list[q][filenames.index(doc + '.txt')])
    doc_row = []
    for doc in doc_list:
        temp  = [doc]
        rel_dic = dict(query_truth[str(q)])
        if doc in rel_dic:
            temp.append(rel_dic[doc])
        else:
            temp.append('Not')
        temp.append(doc_len[filenames.index(doc + '.txt')])
        temp.append(rank_list[q][filenames.index(doc + '.txt')])
        temp.append(round(sim_list[q][filenames.index(doc + '.txt')], 2))
        doc_row.append(temp)

    for row in doc_row:
        index = filenames.index(row[0] + '.txt')
        index_doc = dict(bm25.corpus[index])
        
        for word, freq in  zip(q_words, q_freq):
            if dictionary.doc2bow([word])[0][0] in index_doc: 
                f, s = score_stat(word, freq, index)
                row.append( str(f) + ', ' +  str(round( (s*100)/sim_list[q][index], 1) ))
            else:
                row.append('X')
        ws.append(row)
        
        sec_row = [' ']*5
        temp = []
        for word, freq in index_doc.iteritems():
            if dictionary[word] not in q_words:
                temp.append((dictionary[word], freq, round(bm25.idf[word], 2)))
        ws.append(sec_row + [i[0]  for i in temp])
        ws.append(sec_row + [str(i[1]) + ', ' + str(i[2]) for i in temp])
        ws.append([])        
wb.save(filename = dest_filename)